In [1]:
import logging
logging.basicConfig(level='ERROR')

In [2]:
import pandas as pd

In [3]:
!gdown 1Kr5nfwQ1hdg4VkKPJNmljnc4kdqTyo83 -O SHROOM_test-unlabeled.zip

Downloading...
From: https://drive.google.com/uc?id=1Kr5nfwQ1hdg4VkKPJNmljnc4kdqTyo83
To: /home/slpl/SHROOM_test-unlabeled.zip
100%|█████████████████████████████████████████| 312k/312k [00:00<00:00, 591kB/s]


In [4]:
!unzip -o /home/slpl/SHROOM_test-unlabeled.zip

Archive:  /home/slpl/SHROOM_test-unlabeled.zip
  inflating: SHROOM_test-unlabeled/test.model-agnostic.json  
  inflating: SHROOM_test-unlabeled/test.model-aware.json  


01 : Running With LangChain

In [5]:
import torch
from transformers import BitsAndBytesConfig

quantization_config = BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_compute_dtype=torch.float16,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_use_double_quant=True,
)

In [6]:
model_id = "mistralai/Mistral-7B-Instruct-v0.1"

In [7]:
from transformers import AutoModelForCausalLM, AutoTokenizer, pipeline

In [8]:
model_4bit = AutoModelForCausalLM.from_pretrained( model_id, device_map="auto",quantization_config=quantization_config, )

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

In [9]:
tokenizer = AutoTokenizer.from_pretrained(model_id)

In [10]:
pipeline = pipeline(
        "text-generation",
        model=model_4bit,
        tokenizer=tokenizer,
        use_cache=True,
        device_map="auto",
        max_length=500,
        do_sample=True,
        top_k=5,
        num_return_sequences=1,
        eos_token_id=tokenizer.eos_token_id,
        pad_token_id=tokenizer.eos_token_id,
)

In [11]:
from langchain import HuggingFacePipeline
from langchain import PromptTemplate, LLMChain
llm = HuggingFacePipeline(pipeline=pipeline)

In [12]:
template_mt = """<s>[INST] You are a helpful, respectful and honest assistant.
Answer the following question using this json format: {{answer: (yes, no or maybe), score: (an integer number between 1 and 5, which 1 is for not supported and 5 is for full supported), description: (a description for your answer)}}.
{question} Is the Sentence supported by the Context above? [/INST] </s>
"""
template_pg = """<s>[INST] You are a helpful, respectful and honest assistant.
Answer the following question using this json format: {{answer: (yes, no or maybe), score: (an integer number between 1 and 5, which 1 is for not supported and 5 is for full supported), description: (a description for your answer)}}.
{question} Is the Sentence supported by the Context above? [/INST] </s>
"""
template_dm = """<s>[INST] You are a helpful, respectful and honest assistant.
Answer the following question using this json format: {{answer: (yes, no or maybe), score: (an integer number between 1 and 5, which 1 is for not supported and 5 is for full supported), description: (a description for your answer)}}.
{question} Is the Sentence supported by the Context above? [/INST] </s>
"""

In [13]:
def chat_with_llm(question , template):
    prompt = PromptTemplate(template=template, input_variables=["question"])
    llm_chain = LLMChain(prompt=prompt, llm=llm)
    response = llm_chain.run({"question":question})
    return response

In [14]:
run_on_test = True # whether this baseline system is ran on the test splits or the val splits

In [15]:
#from google.colab import drive
#drive.mount('/content/drive')

In [16]:
import json
import regex

Running on the model-agnostic track data

In [17]:
# change paths appropriately
# make sure the output filename is the same as the reference filename for the scoring program
path_val_model_agnostic = "/home/slpl/SHROOM_test-unlabeled/test.model-agnostic.json"
path_val_model_agnostic_output = "/home/slpl/results/test.model-agnostic.json"

import json
import random
import numpy as np
import tqdm.notebook as tqdm
seed_val = 442
random.seed(seed_val)
np.random.seed(seed_val)

# simple JSON loading
with open(path_val_model_agnostic, 'r') as istr:
    data_val_all = json.load(istr)
num_sample = len(data_val_all)
print(num_sample)

output_json = []
labels = ["Not Hallucination", "Hallucination"]
"""
SelfCheckGPT Usage: (LLM) Prompt
https://github.com/potsawee/selfcheckgpt
Context: {}
Sentence: {}
Is the sentence supported by the context above?
Answer Yes or No:
"""
pattern = regex.compile(r'\{(?:[^{}]|(?R))*\}')
for i in tqdm.trange(num_sample):
    # label = str(data_val_all[i]['label'])
    task = str(data_val_all[i]['task'])
    if run_on_test:
        # test splits will contain ids to ensure correct alignment before scoring
        id = int(data_val_all[i]['id'])
    hyp = str(data_val_all[i]['hyp'])
    src = str(data_val_all[i]['src'])
    tgt = str(data_val_all[i]['tgt'])

    if task == "PG":
        context = f"{src}"
    else: #i.e. task == "MT" or task == "DM":
        context = f"{tgt}"

    message = f"Context: {context}\nSentence: {hyp}\n"
    item_to_json=[]
    idx = 0
    for j in range(10):
      try:
        response = chat_with_llm(message, template_mt)
        answer = str(response.strip().lower()).replace("```", "")
        match = pattern.findall(answer)[0]
        print(match)
        p = json.loads(match)
        item_to_json.append(p)
        idx = idx + 1
        if (idx == 3):
          break;
      except:
        print("An exception occurred")

    if run_on_test:
        item_to_json.append({"id":id})

    output_json.append(item_to_json)

    f = open(path_val_model_agnostic_output, 'w', encoding='utf-8')
    json.dump(output_json, f)
    f.close()
print("done")

1500


  0%|          | 0/1500 [00:00<?, ?it/s]

/home/slpl/.local/lib/python3.8/site-packages/langchain_core/_api/deprecation.py:117: LangChainDeprecationWarning: The function `run` was deprecated in LangChain 0.1.0 and will be removed in 0.2.0. Use invoke instead.
  warn_deprecated(


{
  "answer": "yes",
  "score": 3,
  "description": "the sentence is supported by the context as it suggests that the person's name is not actually tom, which is in line with the context's statement."
}
{
"answer": "maybe",
"score": 3,
"description": "it is possible for the sentence to be supported by the context, as the context does not explicitly state that the speaker's name is tom, but only mentions that the speaker's name may not actually be tom. the speaker could be expressing surprise that their name may not actually be tom, and this could be surprising or unexpected to the person they are speaking to."
}
{
"answer": "maybe",
"score": 3,
"description": "while it is possible that the sentence could be true, it is not clear if it is related to the context. the sentence could have a different meaning or context, and therefore cannot be definitively answered without further information."
}
{
"answer": "maybe",
"score": 3,
"description": "the context suggests that there will be plent

/home/slpl/.local/lib/python3.8/site-packages/transformers/pipelines/base.py:1123: UserWarning: You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset
  warnings.warn(


...

{
"answer": "yes",
"score": 4,
"description": "the sentence 'oh michael, you scare me' is supported by the context given. michael is mentioned as a person who has caused fear, indicating that the sentiment expressed in the sentence is supported by the context."
}


/home/slpl/.local/lib/python3.8/site-packages/transformers/pipelines/base.py:1123: UserWarning: You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset
  warnings.warn(


{
"answer": "maybe",
"score": 3,
"description": "it is possible that the context is related to the sentence, but the relationship is not clear without more context."
}


/home/slpl/.local/lib/python3.8/site-packages/transformers/pipelines/base.py:1123: UserWarning: You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset
  warnings.warn(


{
  "answer": "no",
  "score": 1,
  "description": "the context above does not support the sentence 'oh michael, you scare me'. the context only mentions michael scaring someone, but it does not provide any context about the relationship between michael and the speaker or the reason for the fear."
}
done
